<a href="https://colab.research.google.com/github/Priya170205/composio/blob/master/original_template/Sesame_CSM_(1B)-TTS.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

### News

Placeholder

### Installation

In [6]:
# Install yt-dlp for downloading YouTube audio
# Install pydub for audio conversion
!pip install yt-dlp pydub soundfile



     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 176.0/176.0 kB 4.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.3/3.3 MB 44.6 MB/s eta 0:00:00


In [7]:
# Replace with the YouTube video URL
youtube_url = "https://www.youtube.com/watch?v=FHIml6cRz0k&ab_channel=SandeepMaheshwari"


In [8]:
import os

# Download audio as MP3
!yt-dlp -x --audio-format mp3 {youtube_url}

# List all mp3 files downloaded
mp3_files = [f for f in os.listdir() if f.endswith(".mp3")]
print("Downloaded MP3 files:", mp3_files)



[youtube] Extracting URL: https://www.youtube.com/watch?v=FHIml6cRz0k
[youtube] FHIml6cRz0k: Downloading webpage
[youtube] FHIml6cRz0k: Downloading tv simply player API JSON
[youtube] FHIml6cRz0k: Downloading tv client config
[youtube] FHIml6cRz0k: Downloading player 6742b2b9-main
[youtube] FHIml6cRz0k: Downloading tv player API JSON
[info] FHIml6cRz0k: Downloading 1 format(s): 251
[download] Destination: 99.99% Don’t Know The Self ｜ By Sandeep Maheshwari ｜ Motivational Video Hindi [FHIml6cRz0k].webm
[download] 100% of   19.76MiB in 00:00:00 at 23.34MiB/s
[ExtractAudio] Destination: 99.99% Don’t Know The Self ｜ By Sandeep Maheshwari ｜ Motivational Video Hindi [FHIml6cRz0k].mp3
Deleting original file 99.99% Don’t Know The Self ｜ By Sandeep Maheshwari ｜ Motivational Video Hindi [FHIml6cRz0k].webm (pass -k to keep)
Downloaded MP3 files: ['99.99% Don’t Know The Self ｜ By Sandeep Maheshwari ｜ Motivational Video Hindi [FHIml6cRz0k].mp3']


In [9]:
# Take the first downloaded mp3 file
original_mp3 = mp3_files[0]
new_mp3 = "audio.mp3"

os.rename(original_mp3, new_mp3)
print(f"Renamed '{original_mp3}' to '{new_mp3}'")



Renamed '99.99% Don’t Know The Self ｜ By Sandeep Maheshwari ｜ Motivational Video Hindi [FHIml6cRz0k].mp3' to 'audio.mp3'


In [10]:
from pydub import AudioSegment

# Convert to WAV
audio = AudioSegment.from_mp3(new_mp3)
audio.export("audio.wav", format="wav")
print("Converted to audio.wav")


/usr/local/lib/python3.12/dist-packages/pydub/utils.py:300: SyntaxWarning: invalid escape sequence '\('
  m = re.match('([su]([0-9]{1,2})p?) \(([0-9]{1,2}) bit\)$', token)
/usr/local/lib/python3.12/dist-packages/pydub/utils.py:301: SyntaxWarning: invalid escape sequence '\('
  m2 = re.match('([su]([0-9]{1,2})p?)( \(default\))?$', token)
/usr/local/lib/python3.12/dist-packages/pydub/utils.py:310: SyntaxWarning: invalid escape sequence '\('
  elif re.match('(flt)p?( \(default\))?$', token):
/usr/local/lib/python3.12/dist-packages/pydub/utils.py:314: SyntaxWarning: invalid escape sequence '\('
  elif re.match('(dbl)p?( \(default\))?$', token):


Converted to audio.wav


In [11]:
from pydub import AudioSegment, effects

audio = AudioSegment.from_file("audio.wav")
normalized_audio = effects.normalize(audio)
normalized_audio.export("audio_normalized.wav", format="wav")


<_io.BufferedRandom name='audio_normalized.wav'>

In [12]:
from pydub import AudioSegment

# Load your 30-min audio
audio = AudioSegment.from_file("audio.wav")
os.makedirs("chunks", exist_ok=True)
# Split into 30-second chunks (or 10-second if you want more samples)
chunk_length_ms = 10 * 1000  # 30 seconds
chunks = []
overlap_ms = 2000         # 2-second overlap

for start_ms in range(0, len(audio), chunk_length_ms - overlap_ms):
    chunk = audio[start_ms:start_ms + chunk_length_ms]

for i, start_ms in enumerate(range(0, len(audio), chunk_length_ms)):
    chunk = audio[start_ms:start_ms + chunk_length_ms]
    chunk_name = f"chunks/voice_chunk_{i}.wav"
    chunk.export(chunk_name, format="wav")
    chunks.append(chunk_name)

print("Chunks created:", chunks[:5], "...")  # preview first 5 chunks


Chunks created: ['chunks/voice_chunk_0.wav', 'chunks/voice_chunk_1.wav', 'chunks/voice_chunk_2.wav', 'chunks/voice_chunk_3.wav', 'chunks/voice_chunk_4.wav'] ...


In [13]:
print("Total chunks:", len(chunks))


Total chunks: 164


In [16]:
!pip install faster-whisper

from faster_whisper import WhisperModel
import os # Import the os module

model = WhisperModel("large", device="cuda", compute_type="float16")  # use "cuda" if GPU
chunk_folder = "chunks"
transcripts = []



In [23]:
import json
chunk_folder = "chunks"
chunk_files = sorted([f for f in os.listdir(chunk_folder) if f.endswith(".wav")])

transcripts = []

for idx, file in enumerate(chunk_files):
    path = os.path.join(chunk_folder, file)
    print(f"Starting transcription of chunk {idx+1}/{len(chunk_files)}: {file} ...")

    # Correct call
    segments, info = model.transcribe(path)  # returns tuple

    # Combine segment texts for full chunk text
    text = " ".join([seg.text for seg in segments])

    # Optional: print segments
    for seg in segments:
        print(f"[{seg.start:.2f}s -> {seg.end:.2f}s] {seg.text}")

    # Save results
    transcripts.append({
        "audio": path,
        "text": text,
        "segments": [
            {"segment_text": seg.text, "start": seg.start, "end": seg.end}
            for seg in segments
        ]
    })

    print(f"Chunk {idx+1} done ✅")
     #Save JSON and JSONL
with open("voice_dataset.json", "w") as f:
    json.dump(transcripts, f, indent=2)
with open("voice_dataset.jsonl", "w") as f:
    for entry in transcripts:
        f.write(json.dumps(entry) + "\n")


Starting transcription of chunk 1/164: voice_chunk_0.wav ...
Chunk 1 done ✅
Starting transcription of chunk 2/164: voice_chunk_1.wav ...
Chunk 2 done ✅
Starting transcription of chunk 3/164: voice_chunk_10.wav ...
Chunk 3 done ✅
Starting transcription of chunk 4/164: voice_chunk_100.wav ...
Chunk 4 done ✅
Starting transcription of chunk 5/164: voice_chunk_101.wav ...
Chunk 5 done ✅
Starting transcription of chunk 6/164: voice_chunk_102.wav ...
Chunk 6 done ✅
Starting transcription of chunk 7/164: voice_chunk_103.wav ...
Chunk 7 done ✅
Starting transcription of chunk 8/164: voice_chunk_104.wav ...
Chunk 8 done ✅
Starting transcription of chunk 9/164: voice_chunk_105.wav ...
Chunk 9 done ✅
Starting transcription of chunk 10/164: voice_chunk_106.wav ...
Chunk 10 done ✅
Starting transcription of chunk 11/164: voice_chunk_107.wav ...
Chunk 11 done ✅
Starting transcription of chunk 12/164: voice_chunk_108.wav ...
Chunk 12 done ✅
Starting transcription of chunk 13/164: voice_chunk_109.wav ...

In [24]:
##test
import json

# Load the JSON dataset
with open("voice_dataset.json", "r") as f:
    transcripts = json.load(f)

print(f"Total chunks: {len(transcripts)}")


Total chunks: 164


In [26]:
from IPython.display import Audio, display

# Choose a few random chunks to check
for i in [1,4,3]:  # first 3 chunks
    print(f"--- Chunk {i} ---")
    print("Transcript:", transcripts[i]["text"])
    display(Audio(transcripts[i]["audio"]))


--- Chunk 1 ---
Transcript:  से हुआ जैसे मुझे नेक में भी प्रॉब्लम हुआ था 6 मन्त पहले बैक और नेक में एशू हो गया था उसके जब बैकग्राउंड  गए तो लास्ट 6 महीने से में भूजजा स्क्रॉलिंग कर रहा था वो अल्टीमेटली आकर गया कि पर उस सेल्फ की वजह से


--- Chunk 4 ---
Transcript:  अपने आप आते हैं, उसको cause आपको पता ही नहीं होता है, वो cause कहां पढ़ा हुआ है, memory में पढ़ा हुआ है, कोई अभी movie देखी है, कोई web series देखी है,


--- Chunk 3 ---
Transcript:  कि 99% लोगों तो समझ नहीं आएगी जो मैं कह रहा हूं जो भी मुझे यहां पर वीडियो में देख रहे हैं आप लोग  बैठे हो समझ नहीं आनी क्या बोल गए सर इसको जो भी थॉट्स आते हैं वह अपने आप आते हैं हां


In [28]:
## check for unsloth input



print("Files in current folder:", os.listdir())

# Load JSON
with open("voice_dataset.json", "r") as f:
    transcripts = json.load(f)

print(f"Total chunks loaded: {len(transcripts)}")


Files in current folder: ['.config', 'audio_normalized.wav', 'voice_dataset.json', 'chunks', 'audio.mp3', 'audio.wav', 'voice_dataset.jsonl', 'sample_data']
Total chunks loaded: 164


In [30]:
transcripts = [t for t in transcripts if t["text"].strip() != ""]
print(f"Chunks remaining after removing empty transcripts: {len(transcripts)}")



Chunks remaining after removing empty transcripts: 164


In [31]:
import soundfile as sf

audio_data, sampling_rate = sf.read("audio.wav")
print("Audio length (samples):", len(audio_data))
print("Sampling rate:", sampling_rate)


Audio length (samples): 78574098
Sampling rate: 48000


### Unsloth

`FastModel` supports loading nearly any model now! This includes Vision and Text models!

In [33]:
# Install unsloth
!pip install unsloth[colab-new] torch accelerate peft transformers bitsandbytes trl xformers --upgrade

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 40.1/40.1 kB 2.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 52.3/52.3 kB 4.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.6/11.6 MB 58.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.3/61.3 MB 18.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 544.8/544.8 kB 42.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 117.2/117.2 MB 7.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 491.5/491.5 kB 33.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.3/3.3 MB 49.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 196.0/196.0 kB 14.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 131.7/131.7 kB 12.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 312.9/312.9 kB 22.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 213.6/213.6 kB 16.1 MB/s eta 0:00:00
  Attempting uninstall: tokenizers
    

In [1]:
from unsloth import FastModel
from transformers import CsmForConditionalGeneration
import torch

model, processor = FastModel.from_pretrained(
    model_name = "unsloth/csm-1b",
    max_seq_length= 2048, # Choose any for long context!
    dtype = None, # Leave as None for auto-detection
    auto_model = CsmForConditionalGeneration,
    load_in_4bit = False, # Select True for 4bit - reduces memory usage
)

🦥 Unsloth: Will patch your computer to enable 2x faster free finetuning.
🦥 Unsloth Zoo will now patch everything to make training faster!
==((====))==  Unsloth 2025.8.10: Fast Mimi patching. Transformers: 4.56.0.
   \\   /|    Tesla T4. Num GPUs = 1. Max memory: 14.741 GB. Platform: Linux.
O^O/ \_/ \    Torch: 2.8.0+cu126. CUDA: 7.5. CUDA Toolkit: 12.6. Triton: 3.4.0
\        /    Bfloat16 = FALSE. FA [Xformers = 0.0.32.post2. FA2 = False]
 "-____-"     Free license: http://github.com/unslothai/unsloth
Unsloth: Fast downloading is enabled - ignore downloading bars which are red colored!
Unsloth: QLoRA and full finetuning all not selected. Switching to 16bit LoRA.


model.safetensors:   0%|          | 0.00/4.15G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/264 [00:00<?, ?B/s]

tokenizer_config.json: 0.00B [00:00, ?B/s]

tokenizer.json:   0%|          | 0.00/17.2M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/449 [00:00<?, ?B/s]

chat_template.jinja: 0.00B [00:00, ?B/s]

unsloth/csm-1b does not have a padding token! Will use pad_token = <|PAD_TOKEN|>.


In [2]:
from unsloth import FastModel
from transformers import CsmForConditionalGeneration
import torch

model, processor = FastModel.from_pretrained(
    model_name = "unsloth/csm-1b",
    max_seq_length= 2048, # Choose any for long context!
    dtype = None, # Leave as None for auto-detection
    auto_model = CsmForConditionalGeneration,
    load_in_4bit = True, # Select True for 4bit - reduces memory usage
)

==((====))==  Unsloth 2025.8.10: Fast Mimi patching. Transformers: 4.56.0.
   \\   /|    Tesla T4. Num GPUs = 1. Max memory: 14.741 GB. Platform: Linux.
O^O/ \_/ \    Torch: 2.8.0+cu126. CUDA: 7.5. CUDA Toolkit: 12.6. Triton: 3.4.0
\        /    Bfloat16 = FALSE. FA [Xformers = 0.0.32.post2. FA2 = False]
 "-____-"     Free license: http://github.com/unslothai/unsloth
Unsloth: Fast downloading is enabled - ignore downloading bars which are red colored!
unsloth/csm-1b does not have a padding token! Will use pad_token = <|PAD_TOKEN|>.


We now add LoRA adapters so we only need to update 1 to 10% of all parameters!

In [3]:
model = FastModel.get_peft_model(
    model,
    r = 16, # Choose any number > 0 ! Suggested 8, 16, 32, 64, 128
    target_modules = ["q_proj", "k_proj", "v_proj", "o_proj",
                      "gate_proj", "up_proj", "down_proj",],
    lora_alpha = 32,
    lora_dropout = 0, # Supports any, but = 0 is optimized
    bias = "none",    # Supports any, but = "none" is optimized
    # [NEW] "unsloth" uses 30% less VRAM, fits 2x larger batch sizes!
    use_gradient_checkpointing = "unsloth", # True or "unsloth" for very long context
    random_state = 3407,
    use_rslora = False,  # We support rank stabilized LoRA
    loftq_config = None, # And LoftQ
)

Unsloth: Making `model.base_model.model.backbone_model` require gradients


<a name="Data"></a>
### Data Prep  

We will use the `MrDragonFox/Elise`, which is designed for training TTS models. Ensure that your dataset follows the required format: **text, audio** for single-speaker models or **source, text, audio** for multi-speaker models. You can modify this section to accommodate your own dataset, but maintaining the correct structure is essential for optimal training.

In [4]:
from datasets import Dataset, Audio
import json
import os

# Folder where your chunks are stored
chunk_folder = "chunks"

# Load transcripts (JSONL format)
with open("voice_dataset.jsonl", "r") as f:
    data = [json.loads(line) for line in f]

# Create a list of dicts with file paths
dataset_list = []
for item in data:
    audio_path = item["audio"]
    text = item["text"]
    if os.path.exists(audio_path):
        dataset_list.append({
            "audio": audio_path,  # store path
            "text": text
        })
    else:
        print(f"Warning: File not found: {audio_path}")

# Create HuggingFace Dataset
raw_ds = Dataset.from_list(dataset_list)

# Cast the audio column to datasets.Audio feature type
target_sampling_rate = 24000
raw_ds = raw_ds.cast_column("audio", Audio(sampling_rate=target_sampling_rate))

print(raw_ds)


Dataset({
    features: ['audio', 'text'],
    num_rows: 164
})


In [ ]:
{
    "audio": "chunks/voice_chunk_0.wav",
    "text": "Hello world",
    "speaker_id": 0  # or 1, 2, etc. depending on the speaker
}


In [5]:
#@title Dataset Prep functions
from datasets import load_dataset, Audio, Dataset
import os
from transformers import AutoProcessor
processor = AutoProcessor.from_pretrained("unsloth/csm-1b")

with open("voice_dataset.jsonl", "r") as f:
    data = [json.loads(line) for line in f]

raw_ds = Dataset.from_list(data)


# Getting the speaker id is important for multi-speaker models and speaker consistency
speaker_key = "source"
if "source" not in raw_ds.column_names and "speaker_id" not in raw_ds.column_names:
    print("Unsloth: No speaker found, adding default \"source\" of 0 for all examples")
    new_column = ["0"] * len(raw_ds)
    raw_ds = raw_ds.add_column("source", new_column)
elif "source" not in raw_ds.column_names and "speaker_id" in raw_ds.column_names:
    speaker_key = "speaker_id"

target_sampling_rate = 24000
raw_ds = raw_ds.cast_column("audio", Audio(sampling_rate=target_sampling_rate))

def preprocess_example(example):
    conversation = [
        {
            "role": str(example[speaker_key]),
            "content": [
                {"type": "text", "text": example["text"]},
                {"type": "audio", "path": example["audio"]["array"]},
            ],
        }
    ]

    try:
        model_inputs = processor.apply_chat_template(
            conversation,
            tokenize=True,
            return_dict=True,
            output_labels=True,
            text_kwargs = {
                "padding": "max_length", # pad to the max_length
                "max_length": 256, # this should be the max length of audio
                "pad_to_multiple_of": 8,
                "padding_side": "right",
            },
            audio_kwargs = {
                "sampling_rate": 24_000,
                "max_length": 240001, # max input_values length of the whole dataset
                "padding": "max_length",
            },
            common_kwargs = {"return_tensors": "pt"},
        )
    except Exception as e:
        print(f"Error processing example with text '{example['text'][:50]}...': {e}")
        return None

    required_keys = ["input_ids", "attention_mask", "labels", "input_values", "input_values_cutoffs"]
    processed_example = {}
    # print(model_inputs.keys())
    for key in required_keys:
        if key not in model_inputs:
            print(f"Warning: Required key '{key}' not found in processor output for example.")
            return None

        value = model_inputs[key][0]
        processed_example[key] = value


    # Final check (optional but good)
    if not all(isinstance(processed_example[key], torch.Tensor) for key in processed_example):
         print(f"Error: Not all required keys are tensors in final processed example. Keys: {list(processed_example.keys())}")
         return None

    return processed_example

processed_ds = raw_ds.map(
    preprocess_example,
    remove_columns=raw_ds.column_names,
    desc="Preprocessing dataset",
    num_proc=2
)

preprocessor_config.json:   0%|          | 0.00/271 [00:00<?, ?B/s]

Unsloth: No speaker found, adding default "source" of 0 for all examples


Preprocessing dataset (num_proc=2):   0%|          | 0/164 [00:00<?, ? examples/s]

<a name="Train"></a>
### Train the model
Now let's use Huggingface  `Trainer`! More docs here: [Transformers docs](https://huggingface.co/docs/transformers/main_classes/trainer). We do 60 steps to speed things up, but you can set `num_train_epochs=1` for a full run, and turn off `max_steps=None`.

In [6]:
from transformers import TrainingArguments, Trainer
from unsloth import is_bfloat16_supported

trainer = Trainer(
    model = model,
    train_dataset = processed_ds,
    args = TrainingArguments(
        per_device_train_batch_size = 2,
        gradient_accumulation_steps = 4,
        warmup_steps = 50,
        max_steps = 500,
        learning_rate = 2e-4,
        fp16 = not is_bfloat16_supported(),
        bf16 = is_bfloat16_supported(),
        logging_steps = 5,
        optim = "adamw_8bit",
        weight_decay = 0.01, # Turn this on if overfitting
        lr_scheduler_type = "linear",
        seed = 3407,
        output_dir = "outputs",
        report_to = "none", # Use this for WandB etc
    ),
)

In [ ]:
# @title Show current memory stats
gpu_stats = torch.cuda.get_device_properties(0)
start_gpu_memory = round(torch.cuda.max_memory_reserved() / 1024 / 1024 / 1024, 3)
max_memory = round(gpu_stats.total_memory / 1024 / 1024 / 1024, 3)
print(f"GPU = {gpu_stats.name}. Max memory = {max_memory} GB.")
print(f"{start_gpu_memory} GB of memory reserved.")

In [2]:
trainer_stats = trainer.train()

NameError: name 'trainer' is not defined

In [ ]:
# @title Show final memory and time stats
used_memory = round(torch.cuda.max_memory_reserved() / 1024 / 1024 / 1024, 3)
used_memory_for_lora = round(used_memory - start_gpu_memory, 3)
used_percentage = round(used_memory / max_memory * 100, 3)
lora_percentage = round(used_memory_for_lora / max_memory * 100, 3)
print(f"{trainer_stats.metrics['train_runtime']} seconds used for training.")
print(
    f"{round(trainer_stats.metrics['train_runtime']/60, 2)} minutes used for training."
)
print(f"Peak reserved memory = {used_memory} GB.")
print(f"Peak reserved memory for training = {used_memory_for_lora} GB.")
print(f"Peak reserved memory % of max memory = {used_percentage} %.")
print(f"Peak reserved memory for training % of max memory = {lora_percentage} %.")

<a name="Inference"></a>
### Inference
Let's run the model! You can change the prompts

In [ ]:
from IPython.display import Audio, display
import soundfile as sf

text = "We just finished fine tuning a text to speech model... and it's pretty good!"
speaker_id = 0
inputs = processor(f"[{speaker_id}]{text}", add_special_tokens=True).to("cuda")
audio_values = model.generate(
    **inputs,
    max_new_tokens=125, # 125 tokens is 10 seconds of audio, for longer speech increase this
    # play with these parameters to tweak results
    # depth_decoder_top_k=0,
    # depth_decoder_top_p=0.9,
    # depth_decoder_do_sample=True,
    # depth_decoder_temperature=0.9,
    # top_k=0,
    # top_p=1.0,
    # temperature=0.9,
    # do_sample=True,
    #########################################################
    output_audio=True
)
audio = audio_values[0].to(torch.float32).cpu().numpy()
sf.write("example_without_context.wav", audio, 24000)
display(Audio(audio, rate=24000))

In [ ]:
text = "Sesame is a super cool TTS model which can be fine tuned with Unsloth."

speaker_id = 0
# Another equivalent way to prepare the inputs
conversation = [
    {"role": str(speaker_id), "content": [{"type": "text", "text": text}]},
]
audio_values = model.generate(
    **processor.apply_chat_template(
        conversation,
        tokenize=True,
        return_dict=True,
    ).to("cuda"),
    max_new_tokens=125, # 125 tokens is 10 seconds of audio, for longer speech increase this
    # play with these parameters to tweak results
    # depth_decoder_top_k=0,
    # depth_decoder_top_p=0.9,
    # depth_decoder_do_sample=True,
    # depth_decoder_temperature=0.9,
    # top_k=0,
    # top_p=1.0,
    # temperature=0.9,
    # do_sample=True,
    #########################################################
    output_audio=True
)
audio = audio_values[0].to(torch.float32).cpu().numpy()
sf.write("example_without_context.wav", audio, 24000)
display(Audio(audio, rate=24000))

#### Voice and style consistency

Sesame CSM's power comes from providing audio context for each speaker. Let's pass a sample utterance from our dataset to ground speaker identity and style.

In [ ]:
speaker_id = 0

utterance = raw_ds[3]["audio"]["array"]
utterance_text = raw_ds[3]["text"]
text = "Sesame is a super cool TTS model which can be fine tuned with Unsloth."

# CSM will fill in the audio for the last text.
# You can even provide a conversation history back in as you generate new audio

conversation = [
    {"role": str(speaker_id), "content": [{"type": "text", "text": utterance_text},{"type": "audio", "path": utterance}]},
    {"role": str(speaker_id), "content": [{"type": "text", "text": text}]},
]

inputs = processor.apply_chat_template(
        conversation,
        tokenize=True,
        return_dict=True,
    )
audio_values = model.generate(
    **inputs.to("cuda"),
    max_new_tokens=125, # 125 tokens is 10 seconds of audio, for longer text increase this
    # play with these parameters to tweak results
    # depth_decoder_top_k=0,
    # depth_decoder_top_p=0.9,
    # depth_decoder_do_sample=True,
    # depth_decoder_temperature=0.9,
    # top_k=0,
    # top_p=1.0,
    # temperature=0.9,
    # do_sample=True,
    #########################################################
    output_audio=True
)
audio = audio_values[0].to(torch.float32).cpu().numpy()
sf.write("example_with_context.wav", audio, 24000)
display(Audio(audio, rate=24000))

<a name="Save"></a>
### Saving, loading finetuned models
To save the final model as LoRA adapters, either use Huggingface's `push_to_hub` for an online save or `save_pretrained` for a local save.

**[NOTE]** This ONLY saves the LoRA adapters, and not the full model. To save to 16bit or GGUF, scroll down!

In [ ]:
model.save_pretrained("lora_model")  # Local saving
processor.save_pretrained("lora_model")
# model.push_to_hub("your_name/lora_model", token = "...") # Online saving
# processor.push_to_hub("your_name/lora_model", token = "...") # Online saving

### Saving to float16

We also support saving to `float16` directly. Select `merged_16bit` for float16 or `merged_4bit` for int4. We also allow `lora` adapters as a fallback. Use `push_to_hub_merged` to upload to your Hugging Face account! You can go to https://huggingface.co/settings/tokens for your personal tokens.

In [ ]:
# Merge to 16bit
if False: model.save_pretrained_merged("model", processor, save_method = "merged_16bit",)
if False: model.push_to_hub_merged("hf/model", processor, save_method = "merged_16bit", token = "")

# Merge to 4bit
if False: model.save_pretrained_merged("model", processor, save_method = "merged_4bit",)
if False: model.push_to_hub_merged("hf/model", processor, save_method = "merged_4bit", token = "")

# Just LoRA adapters
if False:
    model.save_pretrained("model")
    processor.save_pretrained("model")
if False:
    model.push_to_hub("hf/model", token = "")
    processor.push_to_hub("hf/model", token = "")
